In [1]:
%reload_ext autoreload
%autoreload 2

# Ejercicio 2: Causal ML

## 0. Introducción

Este notebook tiene como objetivo establecer el tratamiento que se podría dar a la población de una compañía de telecomunicaciones con el fin de reducir la tasa de churn. Para ello se relazará lo siguiente:

1. Exploración de la relación existente entre la variable explicativa y la variable objetivo
2. Determinación de las variables de tratamiento donde se puede tomar una acción y reducir la probabilidad de fuga
3. Planteamiento de la variable de tratamiento y estimación del CATE (empleanod SVC)
4. Estimación del uplift score y selección de la muestra objetivo (10% de la población)

Se procede a la carga de librerías que serán usadas en el notebook:

In [2]:
# Standard library imports
from pathlib import Path
from typing import Dict, Any
import joblib

# Third-party imports
import numpy as np
import pandas as pd


import optuna
from sklearn.base import BaseEstimator, ClassifierMixin
from sklearn.metrics import (
    precision_score, recall_score, f1_score, 
    precision_recall_curve, auc, confusion_matrix,
)
from sklearn.model_selection import (
    train_test_split, RepeatedStratifiedKFold, StratifiedKFold
)
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVC
from imblearn.combine import SMOTEENN
from imblearn.over_sampling import SMOTE
from imblearn.under_sampling import EditedNearestNeighbours
from sklearn.utils import resample
from churn.modelling import ThresholdedSVC
from churn.modelling import (
    eval_model_performance,
    bootstrap_cate,  
    eval_model_performance,
    split_and_subset, 
    custom_f1_scorer,
    objective_causal
)
# CausalML imports
from causalml.inference.meta import BaseSClassifier, BaseTClassifier, BaseXClassifier

# Local application imports
import churn.config as cfg
from churn.paths import create_directories, DATA_DIR
from churn.preprocessing import load_data

from churn.analytics import (
    aggregate_by_variable, 
    display_numeric_results, 
    aggregate_categorical_variables,
    display_categorical_results, 
    perform_ttest,
    calculate_cate_estimates, 
    print_cate_statistics,
    separate_treatment_variable,
    scale_features,
    add_treatment_variable,
    define_cate_variables,
    get_top_customers_for_treatment
    )
from churn.plot import plot_ecdf_plots, create_histogram

from churn.paths import DATA_DIR, MODELS_DIR

# Enable inline plotting for Jupyter notebooks
%matplotlib inline

Se empleará la validación cruzada para evaluar la capacidad de generalización del modelo en datos no vistos. En esta técnica,  el conjunto de datos se divide en múltiples subconjuntos (o "folds"), entrenanándose el modelo en algunos de estos folds y testeámndolo en los folds restantes. Este proceso se repite para obtener una estimación más confiable del rendimiento del modelo. Esto permitirá obtener modelos más robustos de cara a su generalización.

In [3]:
# Define the cross-validation strategy
cv = RepeatedStratifiedKFold(n_splits=cfg.N_SPLITS, n_repeats=cfg.N_REPEATS, random_state=cfg.SEED)

# Check the robustnes of the treatment_effect
kf = StratifiedKFold(n_splits=cfg.N_SPLITS, shuffle=True, random_state=cfg.SEED)

# Initialize the scaler
scaler = StandardScaler()

Se establece el path a los datos del problema

In [5]:
# Path to the raw data
create_directories()
file_path = Path(DATA_DIR / 'churn.parquet')

2024-09-11 11:25:02,195 - INFO - Folder "data" ensured at "/Users/borja/Documents/Somniumrema/projects/ml/churn/data"
2024-09-11 11:25:02,196 - INFO - Folder "models" ensured at "/Users/borja/Documents/Somniumrema/projects/ml/churn/models"


Se cargan los datos del mismo y se comprueban las primeras filas con el fin de tener un primer aceercamiento a los mismos.

In [6]:
# Load the raw data
raw = load_data(file_path) 
# Show the first rows of the raw data
raw.head()

2024-09-11 11:25:04,195 - INFO - Data loaded from /Users/borja/Documents/Somniumrema/projects/ml/churn/data/churn.parquet


area_code  plan  n_sms  total_day_minutes  total_day_calls  \
237522        5.0   2.0    724        1365.991021              203   
847276        2.0   3.0    387        1253.394397              158   
242450        8.0   1.0    490         627.687099              165   
377221        3.0   1.0    822         601.816333              115   
991506        1.0   2.0    455         951.019715              140   

        total_day_charge  total_eve_minutes  total_eve_calls  \
237522         50.449691         681.643301              140   
847276         77.050620         437.941533               88   
242450         42.508170         618.231970               54   
377221         72.020707         605.255759              106   
991506         44.885685         320.538743               75   

        total_eve_charge  total_night_minutes  total_night_calls  \
237522         33.122690           157.639198                 53   
847276         20.629900           220.159029                 32   
242450         17.826781           178.298004                 85   
377221         27.550356           212.695526                 30   
991506         25.209541           217.364011                 98   

        total_night_charge  customer_service_calls  customer_service_rating  \
237522           25.163988                      14                        8   
847276           58.178678                       0                        8   
242450           47.785126                      32                        5   
377221            6.765252                      25                        9   
991506           25.802669                      36                        6   

        customer_hapiness  churn  
237522           0.298234      0  
847276           0.424740      0  
242450           0.378805      1  
377221           0.175085      0  
991506           0.612607      0

Se puede observar como en el caso anterior que existen 16 variables incluyendo la variable objetivo. Como se puede observar el dataset contiene variables de localización, uso, pago y relación con el cliente. Se observa lo siguiente:
- Las variables de uso dichas variables comprenden los minutos u llamdas realizadas en distintos tramos horarios ('day' entre 8h y 19h, 'eve' entre 19h y 22h y 'night' entre 22h y 8h) así como en níumero de mensajes enviados `n_sms`. Adicionalmente las mismas tienen una precisión que se analizará y corregirá posteriormente. Adicionalmente existe una variable categórica `plan` que describe la tarifa empleada por los clientes, que será tratada como categórica.
- La variable de localización únicamente contiene un código de area para los clientes `area_code` que será tratada como categórica.
- las variables de relación con el cliente `customer_service_calls`, `customer_service_rating` y `customer_hapiness` considerna no solamente el número de llamadas realizadas por el cliente al servicio al cliente sino también la calificación de la calidad de la servicio y la satisfacción del cliente.

Por último cabe mencionar la variable `churn` variable objetivo de las acciones que se planteen en este experimento.

In [7]:
# Calculate the proportion of churn and print the results using method chaining
Churn_proportion = (
    raw.assign(churn=pd.to_numeric(raw['churn'], errors='coerce'))
       .loc[:, 'churn']
       .mean()
)

# Print the results
print(f"{Churn_proportion = :.2%}")

Churn_proportion = 8.71%


Se observa que existe un churn inferior al 9%, lo cual es significativamente bajo en comparación con los datos promedios de chrn en el sector un 31% en 2024 según https://customergauge.com/blog/average-churn-rate-by-industry. Se procederá a una limpieza y tipado básico de las variables con el fin de poder continuar con el problema.

In [8]:
# Show the data types of the raw data
raw.info()

<class 'pandas.core.frame.DataFrame'>
Index: 7500 entries, 237522 to 794745
Data columns (total 16 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   area_code                7500 non-null   float64
 1   plan                     7500 non-null   float64
 2   n_sms                    7500 non-null   int64  
 3   total_day_minutes        7500 non-null   float64
 4   total_day_calls          7500 non-null   int64  
 5   total_day_charge         7500 non-null   float64
 6   total_eve_minutes        7500 non-null   float64
 7   total_eve_calls          7500 non-null   int64  
 8   total_eve_charge         7500 non-null   float64
 9   total_night_minutes      7500 non-null   float64
 10  total_night_calls        7500 non-null   int64  
 11  total_night_charge       7500 non-null   float64
 12  customer_service_calls   7500 non-null   int64  
 13  customer_service_rating  7500 non-null   int64  
 14  customer_hapiness     

Se observa que no existen valores faltantes. Adicionalmente no existen observaciones duplicadas. Con respecto al tipado de las mismas, se observa que las variables categóricas `area_code`, `plan` y `churn` no se encuentran tipadas correctamente. Del análisis preliminar del dataset se observa que las variables relacionadas con el uso (i.e. `total_day_calls`, `total_eve_minutes`, `total_eve_minutes`, etc.) en cualquier momento del día pueden ser apriximadas a ningún decimal en el caso de los minutos y llamadas y dos decimales en el caso de los cargos por las mismas.

In [10]:
# Rename column 'customer_hapiness' and apply the correct type to the variables
raw = (
    raw
       .rename(columns={'customer_hapiness': 'customer_happiness'})
       .assign(
    area_code=lambda df: df['area_code'].astype('category'),
    plan=lambda df: df['plan'].astype('category'),
    churn=lambda df: df['churn'].astype('category'),
    total_day_minutes=lambda df: np.round(df['total_day_minutes']),
    total_day_calls=lambda df: np.round(df['total_day_calls']),
    total_day_charge=lambda df: np.round(df['total_day_charge'], 2),
    total_eve_minutes=lambda df: np.round(df['total_eve_minutes']),
    total_eve_calls=lambda df: np.round(df['total_eve_calls']),
    total_night_minutes=lambda df: np.round(df['total_night_minutes']),
    total_night_calls=lambda df: np.round(df['total_night_calls']),
    total_night_charge=lambda df: np.round(df['total_night_charge'], 2)
    )
)

Una vez corregido el tipado de las variables así como renombrada la variable relacionada con la satisfacción del cliente se procede a seleccionar las variables numéricas y a agregar en función de las categorías de chirn las mismas con el fin de analizar la media y mediana de cada uno de los grupos. Aunque a primera vista las variables sobre las que la compañía podría trabajar, accionando medidas preventivas de churn no son las de uso, se ha analizado la relación de todas las variables numéricas por si medidas indirectas pudieran sugerir cambios en el uso del servicio de la compañía.

In [11]:
# Select all numerical columns
variables = raw.select_dtypes(include=[np.number]).columns

# Aggregate the data by the 'churn' variable
results = aggregate_by_variable(raw, variables)

# Dispplay relationships between numerical variables and churn
display_numeric_results(results)

De la agrupación de las variables por su condición de churn se observa lo siguiente:

- Las variables que presentan medias más diferenciadas al comparar los grupos dependiendo de su propensión a la fuga, `customer_service_calls` y `customer_service_rating` presentan los valores más altos. 

- En el caso de `customer_service_calls` existe una diferencia importante (41 llamadas en los que abandonan frente a 9 los que no lo hicieron). Esto indica que existe una relación positivamente correlacionada con `churn` y que es probable que clientes no satisfechos con el servicio llamen a 'servicio al cliente' de esta compañía. Esto sugiere que mejorar la calidad del soporte al cliente podría reducir el `churn`.

- En el caso de `customer_service_rating`, eixste una diferencia baja entre aquellos clientes que no abandonaron la compañía (7/10) frente a los que si lo hicieron (6/(10). Esto sugiere que una baja calificación del servicio por parte del cliente podría ser una cuasa de churn.

- En el caso de `customer_happiness` La falta de variabilidad sugiere que dicha variable podría no ser un buen predictor directo del churn. (considerando como esta recogida) o que no captura adecuadamente los aspectos de la experiencia del cliente que son importantes para retenerlos.
- En cuanto al uso, todas las variables presentan valores muy próximos por lo que no serían variables objetivos. Si bien  pueden estar relacionado con el churn, la diferencia en la media sugiere que el efecto directo de este factor podría ser moderado o débil o que intervienen otras variable. En casi todos los casos la relación es positiva incrementandosé el uso del servicio en el caso de que exista `churn`

El análisis exploratorio confirma la hipótesis inicial con respecto a las variables que pueden accionarse para reducir el `churn` o abandono de clientes de la compañía. En este caso de las tres, parece que `customer_service_calls` sería la más importante, considerándose las otras dos como covariantes de dicha variable al estar todas ellas relacionadas con la interacción al cliente y por lo tanto influir en el posible abandono. Adicionalmente, la variable `customer_service_calls` aunque refleja la frecuencua con la que el cliente contacta el servicio de tantecion al cliente no proporciona información suficiente sobre la calidad de las interacciones lo cual es necesario para entender si estas llamadas influyen en su decisión de fuga. Por lo cual, las variables de `customer_service_rating` y `customer_happines` capturan diferentes aspectos de la experiencia del cliente con el servicio de soporte/atención.

Se procede a analizar para las variables categóricas si existe relación entre el churin y las zonas o planes que los clientes tienen suscritos.

In [12]:
# Aggregate the data by the categorical variables
results = aggregate_categorical_variables(raw, "churn")

# Display relationships between categorical variables and churn
display_categorical_results(results)

Se observa que la media en cada categoría o tramo es muy similar para ambos casos `plan` y `area_code`. Se procede a evaluar gráficamente mediante el empleo de la función empírica de distribución acumulada (ECDF). Distribuciones muy pórximas o superpuestas indicarán que la variable no es significativa respecto al chirn y que la misma no será un factor relevante y curvas separasas significa que la variable si tiene un impacto en churn.

In [13]:
# Plot the ECDF plots for variables
plot_ecdf_plots(raw, raw, 'churn')

Como se puede observar las distribuciones de las variables de uso `n_sms`, `_calls`, `_minutes`, `_charge`, localización `area_code`y tarifa contratada `plan` tiene las dos distribuciónes (azul para 'no churn" y roja para 'churn') muy pórximas o superpuestas por lo que la actuación si fuera osible en las mismas no traería cambios en el churn. 

En lo que respecta a la variable `customer_service_calls`, `customer_service_rating` y `customer_service_happines`,, ambas distribuciones se encuentran alejadas en en caso de fuga o permanencia lo que indica que las variables son significativas. Deberemos poner el foco en elegir entre una de ellas ya que modificaciones en la misma traerán consigo un impacto en la tasa de permanencia (no fuga) de los clientes. 

- En el caso de la variable `customer_service_calls` se observa que en el caso de churn, la curva presenta una mayor pendiente a partir de las 50 llamadas al servicio al cliente por lo que es a partir de ese numero que los clientes tienen una mayor porpensión a la fuga (con una proporción acumulada del 53%). Este valor 50 llamadas podría ser un umbral crítico incrementándose la tasa de churn con las llamdas al tener un mayor número de clientes que abandonan la compañía con cada llamada adicional coparado con valores inferiores a este umbral.

- En el caso de `customer_service_rating` que a partir de valores superiores a 5 en el índice de satisfacción (medido de 0 a 10), la proporción acumulada de clientes que abandonan la compañía es significativamente mayor que los que permanencen. Esta diferencia se ve compensada en el caso en el que el rating es 7 en el que se ve un incremento mayor en aquellos que permanencen frente a los que se fugan compensandose parciamente las tasas acumuladas anteriores. Esto podría inidicar que el rango de valores de actuación en esta variable se encontraría entre estos umbrales críticos para cada categoría (5-7). A partir de 8 las proporciones acumuladas de clientes que se fugan y que permanecen se encuentranb mucho más próximas.

- En el caso de `customer_happines` mientras que para la proporcion de clientes que no fugan crece de forma linea, a partir de valores del 5% la tasa acumulada de clientes que fugan crece significativamente manteniendose casi lineal para valores superiores de dicha variable.

Una vez analizado el comportamiento de estas variables, se procede a analizar la correlación existente entre las variables. Aunque la correlación no mide causalidad, es un promer paso para encontrar dicha causalidad.

In [14]:
# Correlation matrix to identify which features are correlated with churn
correlation_with_churn = raw.corr()['churn'].sort_values(ascending=False) 

# Display results
correlation_with_churn

churn                      1.000000
customer_service_calls     0.523331
total_day_calls            0.028605
n_sms                      0.017339
total_day_minutes          0.009359
total_eve_minutes          0.005191
total_eve_calls            0.004448
total_day_charge           0.001568
area_code                 -0.003627
total_night_calls         -0.004328
total_night_minutes       -0.007464
plan                      -0.008527
total_eve_charge          -0.008758
total_night_charge        -0.010278
customer_service_rating   -0.143524
customer_happiness        -0.224964
Name: churn, dtype: float64

Como puede observarse en la tabla, la correlación existente entre la fuga de un cliente y las llamadas del servicio al cliente es la más alta y positivs indicando que ambas varían en la misma dirección y una la mitad que la otrs aproximadamente. Adicionalmente se puede comprobar como el resto de las variables presentan un orden de maginitud menos en cuanto a su corerelación positiva. En cuanto a la correlación negativa son las variables `customer_happines` y `customer_service_rating` aquellas que presentan una mayor correlación y negativa (pero siempre menor en valor absoluto que la variable `customer_service_calls`).

El análisis anterior confirma que el experimento se realizará sobre la variable `customer_service_calls` considernado como covarantes las variables `customer_happiness` y `customer_service_rating`. En este caso se elige dicha variable no solamente por su relación con churn sino porque es accionable por parte de la compañia pudiendo emprender campañas que dismiuyan el número de llamadas a este servicio, bien mejorando la calidad del servicio telefónico o reduciendo las incidencias relacionadas con el ciclo de vida del cliente en cada periodo de tarificación. En este caso no disponemos de la suficiente información como para poder profundizar en el tipo de acción a realizar.

En este análisis, se va a establecer un umbral de 50 llamadas al mes para diferenciar entre dos grupos:

- **Grupo de control:** Clientes que realizan 50 o más llamadas al mes. Estos clientes no recibirán ningún tratamiento, es decir, mantendrán su número de llamadas.

- **Grupo de tratamiento:** Clientes que realizan más de 50 llamadas al mes. El tratamiento consistirá en reducir el número de llamadas al servicio de atención al cliente a menos de la mitad del máximo que se reciben en la actualidad.

El rango de valores para el número de llamadas oscila entre 0 y 111 llamadas. Reducir el número de llamadas a 50 llamadas al mes es una intervención significativa, y si resulta efectiva, podría estudiarse su sensibilidad. En un futuro, podríamos considerar establecer umbrales inferiores para optimizar aún más la intervención, teniendo en cuenta factores como el coste de las acciones y el impacto en la satisfacción del cliente.

In [15]:
# Define the threshold for the treatment variable:
# Customers with more than 50 customer service calls are considered as treated
threshold = 50

# Create binary treatment variable based on whether the bin is smaller or equal to the threshold
raw['treatment'] = np.where(raw['customer_service_calls'] >= threshold, 1, 0)

In [16]:
# Selecte the most important features
features = ['customer_service_calls', 'customer_service_rating', 'customer_happiness', 'treatment']

# Define the features and target variable
X = raw[features]
y = raw['churn']

Se realiza un split en esntrnamiento y testeo con el fin de obtener datos más robustos en los efectos del tratmiento sobre población que no haya visto el modelo al utilizar un SVC.

In [17]:
# Split the dataset into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(
    X, 
    y, 
    test_size=cfg.TEST_SIZE, 
    random_state=cfg.SEED, 
    stratify=raw['churn']
)

Se procede a establecer de forma explicita la variable de tratamiento anteriormente definida así como a estandarizar los datos con el fin de mejorar las métricas de clasificación de la máquina de soporte vectoral (SVC) para la clasificación. Dicha máquina de soporte vectorial utilizará como en el caso anterior un kernel lineal y se volverán a optimizar los hiperparametros con el fin de obtener el mejor modelo para este caso.

In [18]:
# Column name for the treatment variable
treatment_col = 'treatment'

# Separate the treatment variable
treatment_train, treatment_test, X_train, X_test = separate_treatment_variable(X_train, X_test, treatment_col)

# Scale the features
X_train_scaled, X_test_scaled = scale_features(X_train, X_test, scaler)

# Add the treatment variable back to the scaled datasets
X_train_scaled, X_test_scaled = add_treatment_variable(X_train_scaled, X_test_scaled, treatment_train, treatment_test, treatment_col)

Con el fin de no distorsionar la variable de tratamiento, la misma no es considerada cuando se realiza la estandarización de variables de forma que la misma permanezca con valores binarios. Una vez estandarizados los valores la misma se introduce de nuevo en el dataset. Se reliza la selección y optimización de hiperparametros para un modelo SVC con kernel lineal. 

In [ ]:
# Define the objective function for the causal model
study = optuna.create_study(direction='maximize')

# Optimize the causal model
study.optimize(lambda trial: objective_causal(trial, X_train_scaled, y_train), n_trials = cfg.SEED)

# Get the best trial
best_trial = study.best_trial

# Display the best hyperparameters and the best F1 score
print(f"Best hyperparameters: {best_trial.params}")
print(f'Best F1 Score: {best_trial.value}')

Se emplea como métrica a optimizar (maximizar) la métrica f1 que es una media armonizada entre precisión y recall. Esto se debe a que se considera que los falsos positivos y negativos tendrán igual valor y se quiere mantener un balance adecuado entre los mismos de forma que no se penalice a aquellos que permanecerán en la compaía con campañas dedicadas a aquellos en riesgo de fuga aunque sin embargo aquellas que sean para reducir el número de llamdas tendrá un efecto positivo en ambas poblaciones. El valor del hiperparametro C de tolerancia al error indica que el modelo penalizará significativamente los errores de clasificación frente a los márgenes del hiperplano separado.

Una vez obtenidos los hiperparámetros, se procede a entrenar el modelo en todo el set de entrenamiento con los mejores hiperparámetros y a definir el valor del threshold de probabilidad para las predicciones que optimice la asignación de clases en las predicciones y por lo tanto la métrica elegida.

In [ ]:
# Refit the model on the entire training dataset with the best hyperparameters
svc_model = SVC(C=best_trial.params['C'], kernel='linear', class_weight='balanced', probability=True)

# Handle class imbalance with SMOTEENN
smote_enn = SMOTEENN(smote=SMOTE(sampling_strategy='minority'), enn=EditedNearestNeighbours())
X_train_res, y_train_res = smote_enn.fit_resample(X_train_scaled, y_train)

# Fit the model on the resampled data
svc_model.fit(X_train_res, y_train_res)

# Store the best threshold separately
best_threshold = custom_f1_scorer(y_train, svc_model.predict_proba(X_train_scaled))['best_threshold']

# Print results
print(f'Best Threshold: {best_threshold}')

Se considera un threshold de 0.9, que será el valor utilizado para asignar la clase chun o no churn. Valores de probabilidad superiores clasificarán como churn la observación e inferiores como no churn. Se procede a guardar el modelo empleando este trheshold y serializarlo con el fin de utilizarlo posteriormente en el análisis causal como modelo de base.

In [ ]:
# Save model with best threshold
thresholded_svc = ThresholdedSVC(base_model=svc_model, threshold=best_threshold)

# Serialize the trained model
model_filename = Path(MODELS_DIR / 'thresholded_svc.pkl')
joblib.dump(thresholded_svc, model_filename)

# Inform that the model has been saved
print("Model saved as thresholded_svc.pkl")

In [19]:
# Load the optimized SVC model
model_filename = Path(MODELS_DIR / 'thresholded_svc.pkl')
t_svc_model = joblib.load(model_filename)

# Get the parameters of the loaded SVC model
svc_params = t_svc_model.get_params()
print("SVC Model Parameters:")
print(svc_params)

SVC Model Parameters:
{'base_model__C': 11.599674210852156, 'base_model__break_ties': False, 'base_model__cache_size': 200, 'base_model__class_weight': 'balanced', 'base_model__coef0': 0.0, 'base_model__decision_function_shape': 'ovr', 'base_model__degree': 3, 'base_model__gamma': 'scale', 'base_model__kernel': 'linear', 'base_model__max_iter': -1, 'base_model__probability': True, 'base_model__random_state': None, 'base_model__shrinking': True, 'base_model__tol': 0.001, 'base_model__verbose': False, 'base_model': SVC(C=11.599674210852156, class_weight='balanced', kernel='linear',
    probability=True), 'threshold': 0.9}


Se procede a preparar y entrenar el modelo CATE empleando un Support Vector Classifier (SVC) como base para la clasificación. Este modelo predecirá los efectos de un tratamiento o intervención sobre un resultado, controlando por un conjunto de covariables. Se preparan las variables de entrenamiento y testeo así como las variables de tratamiento y el target. Se emplea el `BaseSClassifier` como modelo de inferencia causal para estomar el efecto del tratamiento condicional medio (CATE) a partir del SVC. Doicho modelo se entrena ajustando la relación entre las covaraibles y el tratsmiento para estimaer el efecto causal del tratamiento sobre el resultado y se realiza la predicción de los mismos en el dataset de testeo.

In [20]:
# Define covariates, treatment, and outcome for the CATE model
X_train_cate, X_test_cate, treatment_train, treatment_test, y_train_cate, y_test_cate = define_cate_variables(X_train_scaled, X_test_scaled, y_train, y_test)

# Initialize the SVC model with the correct parameters
#svc_model = SVC(**svc_params)
cate_model = BaseSClassifier(t_svc_model)

# Train the model
cate_model.fit(
        X=X_train_cate,
        treatment=treatment_train,
        y=y_train
    )
# Predict treatment effects on the test set
treatment_effects = cate_model.predict(X_test_cate)

Una vez entrenado y realzadas las predicciones en el set de testeo se extraen los clientes más propensos a beneficiarse de un tratamiento (reducción del núnero de llamadas por debajko de 20 al servicio al cliente). Dichos efectos se emplean para seleccionar a los principales clientes  (10%) que deberían recibir un tratamiento especial para maximizar la reducción del churn.

Los datos de estos clientes, que estaban escalados, se revierten a su forma original para hacer la selección más interpretable en términos de negocio.

In [21]:
# Get the top customers for treatment
top_customers = get_top_customers_for_treatment(treatment_effects, X_test_scaled, scaler)

# Customers who should receive special treatment to maximize churn reduction.
print("Top 10% customers selected for treatment (unscaled):")
top_customers

Top 10% customers selected for treatment (unscaled):


customer_service_calls  customer_service_rating  customer_happiness  \
956                      7.0                      7.0            0.249786   
1011                     0.0                      7.0            0.250206   
111                      0.0                      8.0            0.131334   
387                      0.0                      8.0            0.148290   
785                     53.0                      9.0            0.030398   
...                      ...                      ...                 ...   
1207                     0.0                      9.0            0.085725   
1761                    34.0                      9.0            0.081126   
1240                    21.0                      8.0            0.204122   
1749                     0.0                      7.0            0.321847   
47                       0.0                      6.0            0.440692   

      Uplift Score  
956       0.910673  
1011      0.910741  
111       0.910793  
387       0.910833  
785       0.911013  
...            ...  
1207      0.914566  
1761      0.914570  
1240      0.914570  
1749      0.914574  
47        0.914575  

[187 rows x 4 columns]

En esta tabla se han seleccionado el 10% de los clientes que se beneficiarían ,ás de la acción. Se puede ver que la reducción de las llamadas de servicio al cliente en clientes con un `customer_happiness` bajo tiene un efecto más significativo que sobre aquellos con un `customer_happiness` alto por lo que a medida que la satiafacción del cliente aumenta parece que el efecto del tratamiento disminuye.

Se precede al análisis del Average Treatment Effect (ATE) para estimar el efecto promedio del tratamiento. En este caso, el tratamiento consiste en reducir el número de llamadas al servicio de atención al cliente para los clientes que superan 50 llamadas al mes. El valor de ATE estimado proporciona una medida del impacto promedio del tratamiento sobre el churn, con un intervalo de confianza que permite evaluar la incertidumbre de esta estimación.


In [35]:
# Select the top 10% of customers who should receive special treatment
top_10_percent_customers = X_test_scaled.nlargest(int(0.1 * len(X_test_scaled)), "customer_service_calls")

# Estimate the CATE for the top 10% of customers
ate_s, ate_s_lb, ate_s_ub = cate_model.estimate_ate(
    X=top_10_percent_customers[["customer_service_rating", "customer_happiness"]].values,  # Variables explicativas
    treatment=top_10_percent_customers["treatment"],  # Tratamiento aplicado
    y=y_test[top_10_percent_customers.index],  # Resultados reales (target) para este grupo
    return_ci=True,  # Devuelve el intervalo de confianza
    bootstrap_ci=False  # Cambia a True si deseas un intervalo con bootstrap
)

# Store the results in a dictionary
ate_values = {
    "Upper_limit (ATE)": ate_s_ub,
    "ATE": ate_s,
    "Lower_limit (ATE)": ate_s_lb
}

# Pritn the results
for description, value in ate_values.items():
    print(f"{description}: {value}")

2024-09-11 11:40:41,691 - INFO - Error metrics for group 1
2024-09-11 11:40:41,693 - INFO -      AUC   (Control):     0.9289
2024-09-11 11:40:41,694 - INFO -      AUC (Treatment):     0.9678
2024-09-11 11:40:41,696 - INFO - Log Loss   (Control):     0.2297
2024-09-11 11:40:41,697 - INFO - Log Loss (Treatment):     0.1874


Upper_limit (ATE): [0.72274707]
ATE: [0.64378209]
Lower_limit (ATE): [0.5648171]


Se observa que el ATE es de aproximadamente 0.64 en la población seleccionada, lo que indica un aumento significativo en el efecto promedio del tratamiento en comparación con el grupo de control. El intervalo de confianza oscila entre 0.56 y 0.72, lo que sugiere que el efecto del tratamiento es estadísticamente robusto y con un margen estrecho de incertidumbre.

 En cuanto a las métricas de rendimiento, se observan mejoras tanto en AUC como en la Log Loss en el grupo tratadofrente al grupo de control. El AUC ** para el grupo tratado es de 0.9678, superior al 0.9289 del grupo de control lo que indica que el modelo es mejor en la clasificación correcta de los clientes tratados en comparación con los no tratados.
 
 En lo que respecta la log loss, Log Loss del grupo tratado es de 0.1874, menor que la del grupo de control, que es de 0.2297, lo que sugiere que el modelo es más preciso en las predicciones para el grupo tratado.

En resumen, los resultados sugieren que el tratamiento aplicado (reducción del número de llamadas) ha tenido un impacto positivo en el comportamiento de los clientes del grupo de tratamiento, con una mejora notable en las métricas de rendimiento del modelo, lo que podría indicar un mejor control del churn o una mayor satisfacción entre los clientes tratados.

In [36]:
# Flatten the treatment_effects array to 1D
treatment_effects_flat = treatment_effects.flatten()

# Create a histogram of the treatment effects
create_histogram(treatment_effects_flat)

Se ve como el efecto del tratamiento es mayor con una frecuencia acumulada mucho mayor por encima de valores superiores a 0.7 en términos de frecuencia que vemos que se acumula de forma significativamente mayor, por lo que tiene el tratamiento efectos positivos. Se procede a analizar el impacto del tratamiento en diferentes grupos de clientes, diferenciados por su calificación del servicio al cliente y nivel de felicidad, covariables introducidas en el estudio.

In [37]:
# Reset the indices of X_test_scaled and y_test to ensure they match
X_test_scaled = X_test_scaled.reset_index(drop=True)
y_test = y_test.reset_index(drop=True)

# Split and subset based on customer service rating (high/low)
rating_threshold = X_test_scaled['customer_service_rating'].median()
high_rating_group, low_rating_group, y_high_rating, y_low_rating = split_and_subset(X_test_scaled, y_test, 'customer_service_rating', rating_threshold)

# Split and subset based on customer happiness (high/low)
happiness_threshold = X_test_scaled['customer_happiness'].median()
high_happiness_group, low_happiness_group, y_high_happiness, y_low_happiness = split_and_subset(X_test_scaled, y_test, 'customer_happiness', happiness_threshold)

# Split and subset based on treatment group (treatment/control)
treatment_threshold = 0.5  # Assuming binary treatment with 0 and 1
treatment_group, control_group, y_treatment, y_control = split_and_subset(X_test_scaled, y_test, 'treatment', treatment_threshold)

In [38]:
# Customer Service Rating Balance Check
perform_ttest(treatment_group, control_group, 'customer_service_rating')

# Customer Happiness Balance Check
perform_ttest(treatment_group, control_group, 'customer_happiness')

T-test for customer_service_rating: t-statistic = 0.8931526502824597, p-value = 0.3718901706524822
T-test for customer_happiness: t-statistic = -0.5332988301409991, p-value = 0.5938900106504137


Para ambas variables se observa que no hay una diferencia estadísticamente significativa en la calificación del servicio entre los grupos de tratamiento y control.

In [39]:
cate_estimates = calculate_cate_estimates(kf, X_test_scaled, y_test, t_svc_model)
print_cate_statistics(cate_estimates)

Mean CATE across folds: 0.08733711133123814
Variance of CATE across folds: 0.00010410645725762553


El valor medio del CATE siendo positivo indica un impacto promedio positivo del tratamiento (8.73%) sobre la población analizada. Asimismo, la baja varianza sugiere que el tratamiento tiene un efecto consistente, y que el modelo no es sensible a la variabilidad de los datos. Se procede a evaluar el ATE, en todos los sugbrupos que se han establecido con las covariables.

In [27]:
# Calculate the overall ATE (mean of all treatment effects)
ATE = np.mean(treatment_effects)
print(f"ATE: {ATE}")

# Calculate and print CATE for specific subgroups and their differences from ATE
subgroups = {
    "High Rating Group": high_rating_group.index,
    "Low Rating Group": low_rating_group.index,
    "High Happiness Group": high_happiness_group.index,
    "Low Happiness Group": low_happiness_group.index,
    "Treatment_Group": treatment_group.index,
    "Control_Group": control_group.index,
}

for name, indices in subgroups.items():
    CATE = treatment_effects[indices].mean()
    print(f"CATE for {name}: {CATE}")
    print(f"Difference between ATE and CATE ({name}): {CATE - ATE}")

ATE: 0.6940362668751154
CATE for High Rating Group: 0.6172859058480032
Difference between ATE and CATE (High Rating Group): -0.07675036102711219
CATE for Low Rating Group: 0.7676588702428156
Difference between ATE and CATE (Low Rating Group): 0.07362260336770021
CATE for High Happiness Group: 0.5682039150656963
Difference between ATE and CATE (High Happiness Group): -0.1258323518094191
CATE for Low Happiness Group: 0.8197344690557399
Difference between ATE and CATE (Low Happiness Group): 0.12569820218062444
CATE for Treatment_Group: 0.7067182463119538
Difference between ATE and CATE (Treatment_Group): 0.012681979436838353
CATE for Control_Group: 0.6935005078772278
Difference between ATE and CATE (Control_Group): -0.0005357589978876032


La tabla muestra un ATE medio global de 0.694, lo que indica que el tratamiento aplicado (reducción del número de llamadas al servicio al cliente) tiene un impacto positivo moderado sobre el churn en toda la población. En lo que se refiere a los distintos subgrupos:

- El impacto del tratamiento en el grupo de clientes con una calificación alta del servicio es 0.617, que es inferior al ATE. La diferencia entre el ATE y el CATE para este grupo es -0.0767, lo que sugiere que el tratamiento tiene menos impacto en los clientes que ya califican bien al servicio. Esto es lógico, ya que estos clientes probablemente ya estén satisfechos, y el tratamiento no les afecta de manera tan significativa.

- El impacto del tratamiento en el grupo de clientes con una calificación baja del servicio es 0.768, que es superior al ATE. La diferencia es +0.0736, lo que indica que el tratamiento tiene mayor impacto en los clientes insatisfechos con el servicio. Esto sugiere que el tratamiento (reducir el número de llamadas) mejora más la experiencia de los clientes insatisfechos.

- El impacto en los clientes con altos niveles de satisfacción es 0.568, que es inferior al ATE. La diferencia es -0.1258, lo que indica que el tratamiento tiene menos impacto en los clientes que están satisfechos ya que estos clientes probablemente ya estén satisfechos con el servicio, y el tratamiento no tiene un impacto significativo en mejorar su experiencia.

- El impacto del tratamiento en los clientes con bajos niveles de satisfacción es 0.820, que es notablemente superior al ATE. La diferencia es +0.1257, lo que sugiere que el tratamiento tiene un impacto mucho mayor en los clientes menos satisfacción, posiblemente mejorando su experiencia de manera significativa.

- El impacto en el grupo tratado es 0.707, que es muy cercano al ATE. La diferencia es de +0.0127, lo que indica que el impacto del tratamiento en el grupo tratado es similar al promedio general. El tratamiento parece estar funcionando como se esperaba para este grupo.

- El impacto en el grupo de control es 0.694, prácticamente igual al ATE. La diferencia es -0.0005, lo que significa que no hay prácticamente ninguna diferencia en el impacto entre el grupo de control y el promedio general.


Por lo tanto, el tratamiento tiene mayor impacto en los subgrupos de clientes insatisfechos o con bajos niveles de felicidad, lo que sugiere que la intervención es más eficaz para mejorar la experiencia de los clientes con problemas.
Sin mebargo, el tratamiento tiene menos impacto en los clientes que ya están satisfechos, lo que es esperable, ya que estos clientes probablemente perciben el servicio de manera positiva y no ven tanto beneficio en la intervención.

Se realizará una prueba placebo para verificar la robustez y validez de los efectos observados en el modelo. en esta prueba se creará una variable de tratamiento ficticia al permutar aleatoriamente los valores del tratamiento original. Esto implica asignar aleatoriamente el tratamiento a los clientes sin seguir el tratamiento original. Se evaluarán los efectos utilizando el mismo modelo que se empleó para estimar los efectos en el grupo tratado real.
Se quiere comprobar es comprobar si los efectos observados en el tratamiento real son verdaderos o si pueden ser explicados por asignaciones aleatorias, para garantizar que los resultados originales.

In [31]:
# Combine X_test_scaled and y_test into one DataFrame
test_model = X_test_scaled.copy()
test_model['churn'] = y_test  # Add the target variable

# Perform the placebo test
test_model['placebo_treatment'] = np.random.permutation(test_model['treatment'])

# Subset the placebo group and get treatment effects
placebo_group = test_model[test_model['placebo_treatment'] == 1]
X_placebo = placebo_group.drop(columns=['churn', 'placebo_treatment'])
y_placebo = placebo_group['churn']

# Predict treatment effects and calculate CATE for the placebo group
placebo_effects = t_svc_model.predict_proba(X_placebo)[:, 1]
CATE_placebo = np.mean(placebo_effects)

print(f"CATE for Placebo Group: {CATE_placebo}")


CATE for Placebo Group: 0.16613875762806718


En este caso, un CATE de 0.1661 sugiere que el modelo detecta un pequeño efecto, pero este valor es significativamente menor que los efectos observados en los análisis reales de tratamiento, por lo que los resultados del tratamiento son válidos y no simplemente debidos al azar.

Se procede a analizar las métricas de clasificación del modelo para cada subgrupo establecido anteriormente

In [32]:
high_rating_results = eval_model_performance(t_svc_model, high_rating_group, y_high_rating, subgroup_name="High Customer Service Rating Group")
low_rating_results = eval_model_performance(t_svc_model, low_rating_group, y_low_rating, subgroup_name="Low Customer Service Rating Group")

--- High Customer Service Rating Group ---
Precision: 0.7142857142857143
Recall: 0.5737704918032787
F1-Score: 0.6363636363636364
PR AUC: 0.7389967860059844
Confusion Matrix:
[[843  14]
 [ 26  35]]
--- Low Customer Service Rating Group ---
Precision: 0.7204301075268817
Recall: 0.6568627450980392
F1-Score: 0.6871794871794872
PR AUC: 0.7610918356803221
Confusion Matrix:
[[829  26]
 [ 35  67]]


El modelo tiene un rendimiento ligeramente mejor en el grupo de baja calificación del servicio al cliente, como  indican  valores más elevados de Recall, F1-Score, y PR AUC. La precision es similar en ambos grupos, pero el grupo de baja calificación tiene un mejor recall, lo que sugiere que el modelo es más efectivo al identificar clientes en riesgo de churn entre aquellos que están menos satisfechos con el servicio.
La matriz de confusión muestra que hay más falsos negativos en el grupo de baja calificación (35 frente a 26 en el grupo de alta calificación), lo que podría significar que aún hay margen para mejorar en la identificación correcta de estos clientes.

In [33]:
high_happiness_results = eval_model_performance(t_svc_model, high_happiness_group, y_high_happiness, subgroup_name="High Customer Happiness Group")
low_happiness_results = eval_model_performance(t_svc_model, low_happiness_group, y_low_happiness, subgroup_name="Low Customer Happiness Group")

--- High Customer Happiness Group ---
Precision: 0.6052631578947368
Recall: 0.7666666666666667
F1-Score: 0.6764705882352942
PR AUC: 0.688300116732758
Confusion Matrix:
[[892  15]
 [  7  23]]
--- Low Customer Happiness Group ---
Precision: 0.7596153846153846
Recall: 0.5939849624060151
F1-Score: 0.6666666666666666
PR AUC: 0.7783527234326738
Confusion Matrix:
[[780  25]
 [ 54  79]]


El modelo parece ser más efectivo en identificar clientes con baja satisfacción que están en riesgo de churn, ya que tiene una mejor precision y un PR AUC más alto. Sin embargo, en el grupo de alta felicidad, aunque el recall es alto, es importante mejorar la precision para reducir los falsos positivos. por lo tanto, modelo está mejor diseñado para clientes menos satisfechos, pero se podría ajustar para mejorar su capacidad de detección en clientes más satisfechos sin aumentar los falsos positivos.